In [3]:
import pandas as pd

In [4]:
df_data=pd.read_excel(r'C:\Users\sanjay_godiya\Desktop\MyDocs\DataScience\Lab_data\BBMP_Ward_Master_2011.xlsx',
                      sheet_name='Sheet1')

In [5]:
df_data.head(10)

Ward_Name  Population_density_(persons_per_sq_km)
0           Kempegowda Ward                                    3182
1          Chowdeswari Ward                                    5635
2                    Atturu                                    6606
3  Yelahanka Satellite Town                                    9224
4                   Jakkuru                                    2215
5               Thanisandra                                    7161
6           Byatarayanapura                                    7198
7               Kodigehalli                                   12369
8            Vidyaranyapura                                    5753
9         Dodda Bommasandra                                    8673

In [6]:
df_data.shape

(198, 2)

In [7]:
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import folium # map rendering library

In [8]:
def getBlrData(ward_name,population_density):
    data=[]
    for name,density in zip (ward_name,population_density):
        row=[]
        address = name +', Bangalore, India'
        geolocator = Nominatim(user_agent="ny_explorer")
        location = geolocator.geocode(address)
        if location is not None:
            lat = location.latitude
            long = location.longitude
            row.append(name)
            row.append(density)
            row.append(lat)
            row.append(long)
        data.append(row)
    return(data)

In [9]:
df_data['Ward_Name']=df_data['Ward_Name'].str.replace('Ward','')
df_data.columns=df_data.columns.str.strip()
blr_data=getBlrData(ward_name=df_data['Ward_Name'],
                    population_density=df_data['Population_density_(persons_per_sq_km)'])

In [10]:
Bangalore_df=pd.DataFrame(blr_data,columns=['Neighbourhood','Population_density_(persons_per_sq_km)','Latitude','Longitude'])
Bangalore_df.dropna(how='any',inplace=True)
Bangalore_df['Population_density_(persons_per_sq_km)']=Bangalore_df['Population_density_(persons_per_sq_km)'].astype(int)
Bangalore_df.head()

Neighbourhood  Population_density_(persons_per_sq_km)  \
0               Kempegowda                                     3182   
1              Chowdeswari                                     5635   
2                    Atturu                                    6606   
3  Yelahanka Satellite Town                                    9224   
4                   Jakkuru                                    2215   

    Latitude  Longitude  
0  13.109018  77.601900  
1  13.120459  77.579618  
2  13.100409  77.858725  
3  13.089139  77.582717  
4  13.098320  77.625146

In [11]:
Bangalore_df.shape

(168, 4)

In [12]:
address = 'Bangalore, India'
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
blr_lat = location.latitude
blr_long = location.longitude
print('The geograpical coordinates of Bangalore are {}, {}.'.format(blr_lat, blr_long))

The geograpical coordinates of Bangalore are 12.9791198, 77.5912997.


In [13]:
import folium
map_blr = folium.Map(location=[blr_lat, blr_long], zoom_start=10)
# add markers to map
for lat, lng, label,density in zip(Bangalore_df['Latitude'], Bangalore_df['Longitude'], Bangalore_df['Neighbourhood'],
                           Bangalore_df['Population_density_(persons_per_sq_km)']):
    label = folium.Popup(label+','+ str(density), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='yellow',
        fill_opacity=0.7,
        parse_html=False).add_to(map_blr) 
map_blr

Defining Foursquare Credentials and Version<br>
I will utilize the Foursquare API to explore the neighborhoods and segment them.

In [14]:
CLIENT_ID = '2DQXYXWZHVQTGCZ5IUOZBKG5ISOK3YQD1TTA5H3L5LSZAHPZ' #Foursquare ID
CLIENT_SECRET = 'CGB5ZQHLGAIPP3H45JNKLDJRBH5PCMZSDGKEHSQ0KZUKGKWL' #Foursquare Secret
VERSION = '20180605' # Foursquare API version

Creating a function to explore 100 venues at each loaction within 1000 radius

In [15]:
import requests
LIMIT=500
def getNearbyVenues(names,densities,latitudes,longitudes,radius=2000):   
    venues_list=[]
    for name,dens,lat,lng in zip(names,densities,latitudes,longitudes):
            
        # API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID,CLIENT_SECRET,VERSION,lat,lng,radius,LIMIT)
            
        # GET request
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        # append only relevant information for each nearby venue
        venues_list.append([(name,dens,lat,lng,v['venue']['name'],v['venue']['location']['lat'],v['venue']['location']['lng'],
                             v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood','Population_density_(persons_per_sq_km)','Latitude','Longitude',
                             'Venue','Venue_Latitude','Venue_Longitude', 'Venue_Category']
    
    return(nearby_venues)

In [16]:
blr_venues = getNearbyVenues(names=Bangalore_df['Neighbourhood'],densities=Bangalore_df['Population_density_(persons_per_sq_km)'],
                             latitudes=Bangalore_df['Latitude'],longitudes=Bangalore_df['Longitude'])
blr_venues

Neighbourhood  Population_density_(persons_per_sq_km)  \
0                  Kempegowda                                     3182   
1                  Kempegowda                                     3182   
2                  Kempegowda                                     3182   
3                  Kempegowda                                     3182   
4                  Kempegowda                                     3182   
5                  Kempegowda                                     3182   
6                  Kempegowda                                     3182   
7                  Kempegowda                                     3182   
8                  Kempegowda                                     3182   
9                  Kempegowda                                     3182   
10                 Kempegowda                                     3182   
11                 Kempegowda                                     3182   
12                 Kempegowda                                     3182   
13                 Kempegowda                                     3182   
14                Chowdeswari                                     5635   
15                Chowdeswari                                     5635   
16                Chowdeswari                                     5635   
17                Chowdeswari                                     5635   
18                Chowdeswari                                     5635   
19                Chowdeswari                                     5635   
20                Chowdeswari                                     5635   
21                      Atturu                                    6606   
22                      Atturu                                    6606   
23                      Atturu                                    6606   
24                      Atturu                                    6606   
25                      Atturu                                    6606   
26    Yelahanka Satellite Town                                    9224   
27    Yelahanka Satellite Town                                    9224   
28    Yelahanka Satellite Town                                    9224   
29    Yelahanka Satellite Town                                    9224   
...                        ...                                     ...   
8181               Vasanthpura                                   10852   
8182               Vasanthpura                                   10852   
8183               Vasanthpura                                   10852   
8184               Vasanthpura                                   10852   
8185               Vasanthpura                                   10852   
8186               Vasanthpura                                   10852   
8187               Vasanthpura                                   10852   
8188               Vasanthpura                                   10852   
8189               Vasanthpura                                   10852   
8190               Vasanthpura                                   10852   
8191               Vasanthpura                                   10852   
8192               Vasanthpura                                   10852   
8193               Vasanthpura                                   10852   
8194               Vasanthpura                                   10852   
8195               Vasanthpura                                   10852   
8196               Vasanthpura                                   10852   
8197               Vasanthpura                                   10852   
8198               Vasanthpura                                   10852   
8199               Vasanthpura                                   10852   
8200               Vasanthpura                                   10852   
8201               Vasanthpura                                   10852   
8202               Vasanthpura                                   10852   
8203               Va

In [17]:
blr_venues['Venue_Category'].value_counts()

Indian Restaurant                  1348
Café                                492
Fast Food Restaurant                376
Ice Cream Shop                      363
Coffee Shop                         294
Pizza Place                         280
Chinese Restaurant                  202
Hotel                               188
Bakery                              186
Department Store                    145
Vegetarian / Vegan Restaurant       134
Lounge                              133
Italian Restaurant                  127
Breakfast Spot                      125
Snack Place                         114
Restaurant                          108
Park                                107
Asian Restaurant                    104
Sandwich Place                      104
Clothing Store                      101
Shopping Mall                        93
Gym                                  88
Brewery                              87
Dessert Shop                         85
Multiplex                            83


In [44]:
blr_restaurants=blr_venues[blr_venues['Venue_Category'].str.contains('Restaurant')]
blr_restaurants_grouped=blr_restaurants.groupby(['Neighbourhood','Venue_Category','Population_density_(persons_per_sq_km)'])[['Venue_Category']].count()

In [45]:
blr_restaurants_grouped=blr_restaurants_grouped.add_suffix('_Count').reset_index()
blr_restaurants_grouped

Neighbourhood                   Venue_Category  \
0               A Narayanapura                 Asian Restaurant   
1               A Narayanapura             Fast Food Restaurant   
2               A Narayanapura                Indian Restaurant   
3               A Narayanapura               Italian Restaurant   
4               A Narayanapura               Mexican Restaurant   
5               A Narayanapura          New American Restaurant   
6                      Adugodi                Andhra Restaurant   
7                      Adugodi                 Asian Restaurant   
8                      Adugodi               Chinese Restaurant   
9                      Adugodi             Fast Food Restaurant   
10                     Adugodi                 Halal Restaurant   
11                     Adugodi                Indian Restaurant   
12                     Adugodi               Italian Restaurant   
13                     Adugodi             Karnataka Restaurant   
14                     Adugodi                Kerala Restaurant   
15                     Adugodi        Middle Eastern Restaurant   
16                     Adugodi  Southern / Soul Food Restaurant   
17                     Adugodi                  Thai Restaurant   
18                      Agaram                 Asian Restaurant   
19                      Agaram               Chinese Restaurant   
20                      Agaram             Fast Food Restaurant   
21                      Agaram                Indian Restaurant   
22                      Agaram               Italian Restaurant   
23                      Agaram                Korean Restaurant   
24                      Agaram               Mexican Restaurant   
25                      Agaram        Middle Eastern Restaurant   
26                      Agaram                       Restaurant   
27                      Agaram               Seafood Restaurant   
28                      Agaram          South Indian Restaurant   
29                      Agaram    Vegetarian / Vegan Restaurant   
...                        ...                              ...   
1101        Vishveshwara Puram              Japanese Restaurant   
1102        Vishveshwara Puram                       Restaurant   
1103        Vishveshwara Puram          South Indian Restaurant   
1104        Vishveshwara Puram    Vegetarian / Vegan Restaurant   
1105   Vishwanath Nagenahalli                Chinese Restaurant   
1106   Vishwanath Nagenahalli              Fast Food Restaurant   
1107   Vishwanath Nagenahalli                 Indian Restaurant   
1108   Vishwanath Nagenahalli                Punjabi Restaurant   
1109   Vishwanath Nagenahalli     Vegetarian / Vegan Restaurant   
1110  Yelahanka Satellite Town              American Restaurant   
1111  Yelahanka Satellite Town                Indian Restaurant   
1112  Yelahanka Satellite Town          South Indian Restaurant   
1113             Yelchenahalli               Chinese Restaurant   
1114             Yelchenahalli                Indian Restaurant   
1115             Yelchenahalli               Seafood Restaurant   
1116             Yelchenahalli          South Indian Restaurant   
1117             Yelchenahalli    Vegetarian / Vegan Restaurant   
1118             Yeshwanthpura                 Asian Restaurant   
1119             Yeshwanthpura               Chinese Restaurant   
1120             Yeshwanthpura             Fast Food Restaurant   
1121             Yeshwanthpura                French Restaurant   
1122             Yeshwanthpura                German Restaurant   
1123             Yeshwanthpura                Indian Restaurant   
1124             Yeshwanthpura               Italian Restaurant   
1125             Yeshwanthpura         Mediterranean Restaurant   
1126             Yeshwanthpura               Mexican Restaurant   
1127             Yeshwanthpura                       Restaurant   
1128             Yeshwanthpura               Seafood Restaurant 

In [46]:
blr_restaurants_grouped.sort_values(by=['Population_density_(persons_per_sq_km)'],ascending=False)

Neighbourhood                 Venue_Category  \
789   Padarayanapura              Indian Restaurant   
788   Padarayanapura           Fast Food Restaurant   
767       Nilasandra           Fast Food Restaurant   
768       Nilasandra              Indian Restaurant   
776       Nilasandra             Seafood Restaurant   
774       Nilasandra             Persian Restaurant   
773       Nilasandra      Middle Eastern Restaurant   
772       Nilasandra             Mexican Restaurant   
771       Nilasandra       Mediterranean Restaurant   
770       Nilasandra              Kerala Restaurant   
769       Nilasandra             Italian Restaurant   
775       Nilasandra             Punjabi Restaurant   
766       Nilasandra             Chinese Restaurant   
968    Shivaji Nagar            Japanese Restaurant   
965    Shivaji Nagar          Hyderabadi Restaurant   
958    Shivaji Nagar              Afghan Restaurant   
959    Shivaji Nagar            American Restaurant   
960    Shivaji Nagar              Andhra Restaurant   
961    Shivaji Nagar             Chinese Restaurant   
962    Shivaji Nagar    Eastern European Restaurant   
963    Shivaji Nagar           Fast Food Restaurant   
964    Shivaji Nagar              French Restaurant   
972    Shivaji Nagar        South Indian Restaurant   
971    Shivaji Nagar             Seafood Restaurant   
970    Shivaji Nagar           Pakistani Restaurant   
969    Shivaji Nagar      Middle Eastern Restaurant   
967    Shivaji Nagar             Italian Restaurant   
966    Shivaji Nagar              Indian Restaurant   
864        Rayapuram           Fast Food Restaurant   
865        Rayapuram              Indian Restaurant   
...              ...                            ...   
429             Hudi           Karnataka Restaurant   
19            Agaram             Chinese Restaurant   
20            Agaram           Fast Food Restaurant   
21            Agaram              Indian Restaurant   
29            Agaram  Vegetarian / Vegan Restaurant   
23            Agaram              Korean Restaurant   
27            Agaram             Seafood Restaurant   
26            Agaram                     Restaurant   
25            Agaram      Middle Eastern Restaurant   
18            Agaram               Asian Restaurant   
24            Agaram             Mexican Restaurant   
28            Agaram        South Indian Restaurant   
22            Agaram             Italian Restaurant   
594      Kempegowda             American Restaurant   
595      Kempegowda               Indian Restaurant   
596      Kempegowda         South Indian Restaurant   
597      Kempegowda   Vegetarian / Vegan Restaurant   
129       Bellanduru             Tex-Mex Restaurant   
128       Bellanduru             Punjabi Restaurant   
126       Bellanduru              Kerala Restaurant   
127       Bellanduru        North Indian Restaurant   
125       Bellanduru             Italian Restaurant   
124       Bellanduru              Indian Restaurant   
123       Bellanduru           Fast Food Restaurant   
122       Bellanduru    Eastern European Restaurant   
121       Bellanduru               Asian Restaurant   
120       Bellanduru            American Restaurant   
119       Bellanduru              Afghan Restaurant   
443          Jakkuru              Indian Restaurant   
1053         Varthur              Indian Restaurant   

      Population_density_(persons_per_sq_km)  Venue_Category_Count  
789                                   118059                     7  
788                                   118059                     2  
767                                    94287                     2  
768                                    94287                    16  
776                                    94287                     1  
774                                    94287                     1  
773                                    94287                     1  
772                                    94287

In [47]:
#Plotting Bangalore Restaurants
map_blr_venues = folium.Map(location=[blr_lat, blr_long], zoom_start=10)
# add markers to map
for lat, lng, label,neigh in zip(blr_restaurants['Venue_Latitude'], blr_restaurants['Venue_Longitude'], 
                                 blr_restaurants['Venue_Category'],
                                 blr_restaurants['Neighbourhood']):
    label = folium.Popup(label+','+neigh, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='yellow',
        fill_opacity=0.7,
        parse_html=False).add_to(map_blr_venues) 
map_blr_venues

In [98]:
#Top 10 most dens areas of Bangalore
top10_dens=Bangalore_df[['Neighbourhood','Population_density_(persons_per_sq_km)']].sort_values(by='Population_density_(persons_per_sq_km)',ascending=False).head(10)
top10_dens

Neighbourhood  Population_density_(persons_per_sq_km)
134      Padarayanapura                                  118059
121  Kempapura Agrahara                                  113291
115          Nilasandra                                   94287
91        Shivaji Nagar                                   87856
136           Rayapuram                                   81770
96      Dayananda Nagar                                   80035
47     Muneshwara Nagar                                   74511
133        Bapuji Nagar                                   72549
170     Gurappana Palya                                   72068
29     Kadugondanahalli                                   65514

In [99]:
#Top 10 least dens areas of Bangalore
least10_dens=Bangalore_df[['Neighbourhood','Population_density_(persons_per_sq_km)']].sort_values(by='Population_density_(persons_per_sq_km)',ascending=True).head(10)
least10_dens

Neighbourhood  Population_density_(persons_per_sq_km)
197   Hemmigepura                                    1652
148       Varthur                                    1929
4         Jakkuru                                    2215
149    Bellanduru                                    3041
0     Kempegowda                                     3182
113        Agaram                                    3345
53           Hudi                                    3349
82       Kadugodi                                    3934
195    Anjanapura                                    3997
83        Hagadur                                    4003

In [120]:
#Top 10 most dens areas with restaurants counts
blr_restaurants_grouped[blr_restaurants_grouped.Neighbourhood.isin(top10_dens['Neighbourhood'].tolist())].sort_values(by='Population_density_(persons_per_sq_km)',ascending=False)

Neighbourhood                 Venue_Category  \
788    Padarayanapura           Fast Food Restaurant   
789    Padarayanapura              Indian Restaurant   
773        Nilasandra      Middle Eastern Restaurant   
766        Nilasandra             Chinese Restaurant   
767        Nilasandra           Fast Food Restaurant   
768        Nilasandra              Indian Restaurant   
769        Nilasandra             Italian Restaurant   
770        Nilasandra              Kerala Restaurant   
771        Nilasandra       Mediterranean Restaurant   
772        Nilasandra             Mexican Restaurant   
774        Nilasandra             Persian Restaurant   
775        Nilasandra             Punjabi Restaurant   
776        Nilasandra             Seafood Restaurant   
959     Shivaji Nagar            American Restaurant   
961     Shivaji Nagar             Chinese Restaurant   
972     Shivaji Nagar        South Indian Restaurant   
958     Shivaji Nagar              Afghan Restaurant   
963     Shivaji Nagar           Fast Food Restaurant   
962     Shivaji Nagar    Eastern European Restaurant   
960     Shivaji Nagar              Andhra Restaurant   
964     Shivaji Nagar              French Restaurant   
966     Shivaji Nagar              Indian Restaurant   
971     Shivaji Nagar             Seafood Restaurant   
967     Shivaji Nagar             Italian Restaurant   
968     Shivaji Nagar            Japanese Restaurant   
969     Shivaji Nagar      Middle Eastern Restaurant   
970     Shivaji Nagar           Pakistani Restaurant   
965     Shivaji Nagar          Hyderabadi Restaurant   
865         Rayapuram              Indian Restaurant   
864         Rayapuram           Fast Food Restaurant   
..                ...                            ...   
100      Bapuji Nagar                     Restaurant   
101      Bapuji Nagar             Seafood Restaurant   
99       Bapuji Nagar              Indian Restaurant   
323   Gurappana Palya      Middle Eastern Restaurant   
327   Gurappana Palya        South Indian Restaurant   
320   Gurappana Palya             Italian Restaurant   
321   Gurappana Palya       Mediterranean Restaurant   
322   Gurappana Palya             Mexican Restaurant   
324   Gurappana Palya             Punjabi Restaurant   
325   Gurappana Palya          Rajasthani Restaurant   
326   Gurappana Palya                     Restaurant   
328   Gurappana Palya  Vegetarian / Vegan Restaurant   
318   Gurappana Palya               Halal Restaurant   
317   Gurappana Palya           Fast Food Restaurant   
316   Gurappana Palya             Dim Sum Restaurant   
315   Gurappana Palya        Comfort Food Restaurant   
314   Gurappana Palya             Chinese Restaurant   
313   Gurappana Palya               Asian Restaurant   
312   Gurappana Palya              Andhra Restaurant   
319   Gurappana Palya              Indian Restaurant   
570  Kadugondanahalli        South Indian Restaurant   
561  Kadugondanahalli              Andhra Restaurant   
562  Kadugondanahalli             Chinese Restaurant   
563  Kadugondanahalli           Fast Food Restaurant   
564  Kadugondanahalli              Indian Restaurant   
565  Kadugondanahalli              Kerala Restaurant   
566  Kadugondanahalli              Korean Restaurant   
567  Kadugondanahalli       Mediterranean Restaurant   
568  Kadugondanahalli      Middle Eastern Restaurant   
569  Kadugondanahalli           Pakistani Restaurant   

     Population_density_(persons_per_sq_km)  Venue_Category_Count  
788                                  118059                     2  
789                                  118059                     7  
773                                   94287                     1  
766                                   94287                     4  
767                                   94287                     2  
768                                   94287                    16  
769                                   94287                

In [121]:
#Top 10 least dens areas with restaurants counts
blr_restaurants_grouped[blr_restaurants_grouped.Neighbourhood.isin(least10_dens['Neighbourhood'].tolist())].sort_values(by='Population_density_(persons_per_sq_km)',ascending=True)

Neighbourhood                 Venue_Category  \
1053       Varthur              Indian Restaurant   
443        Jakkuru              Indian Restaurant   
129     Bellanduru             Tex-Mex Restaurant   
127     Bellanduru        North Indian Restaurant   
126     Bellanduru              Kerala Restaurant   
125     Bellanduru             Italian Restaurant   
124     Bellanduru              Indian Restaurant   
123     Bellanduru           Fast Food Restaurant   
122     Bellanduru    Eastern European Restaurant   
121     Bellanduru               Asian Restaurant   
120     Bellanduru            American Restaurant   
119     Bellanduru              Afghan Restaurant   
128     Bellanduru             Punjabi Restaurant   
596    Kempegowda         South Indian Restaurant   
595    Kempegowda               Indian Restaurant   
594    Kempegowda             American Restaurant   
597    Kempegowda   Vegetarian / Vegan Restaurant   
28          Agaram        South Indian Restaurant   
19          Agaram             Chinese Restaurant   
29          Agaram  Vegetarian / Vegan Restaurant   
20          Agaram           Fast Food Restaurant   
18          Agaram               Asian Restaurant   
22          Agaram             Italian Restaurant   
27          Agaram             Seafood Restaurant   
26          Agaram                     Restaurant   
25          Agaram      Middle Eastern Restaurant   
23          Agaram              Korean Restaurant   
24          Agaram             Mexican Restaurant   
21          Agaram              Indian Restaurant   
429           Hudi           Karnataka Restaurant   
560       Kadugodi  Vegetarian / Vegan Restaurant   
559       Kadugodi           Fast Food Restaurant   
558       Kadugodi               Asian Restaurant   
373        Hagadur                     Restaurant   
371        Hagadur              Kerala Restaurant   
370        Hagadur             Italian Restaurant   
369        Hagadur              Indian Restaurant   
367        Hagadur    Eastern European Restaurant   
366        Hagadur             Chinese Restaurant   
365        Hagadur               Asian Restaurant   
364        Hagadur            American Restaurant   
372        Hagadur          Rajasthani Restaurant   
368        Hagadur           Fast Food Restaurant   

      Population_density_(persons_per_sq_km)  Venue_Category_Count  
1053                                    1929                     1  
443                                     2215                     1  
129                                     3041                     1  
127                                     3041                     1  
126                                     3041                     1  
125                                     3041                     1  
124                                     3041                     9  
123                                     3041                     5  
122                                     3041                     1  
121                                     3041                     1  
120                                     3041                     1  
119                                     3041                     1  
128                                     3041                     1  
596                                     3182                     1  
595                                     3182                     1  
594                                     3182                     1  
597                                     3182                     1  
28                                      3345                     1  
19                                      3345                     2  
29                                      3345                     2  
20                                      3345                     3  
18                                      3345                     1  
22                                      3345                     3  
27              